Using Fbprophet solves the problem by automating minor tweaking on their side.


Prophet library can automatically manage parameters related to seasonality and data stationarity


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
import torch

# If there's a GPU available...
if torch.cuda.is_available():    

    # Tell PyTorch to use the GPU.    
    device = torch.device("cuda")

    print('There are %d GPU(s) available.' % torch.cuda.device_count())

    print('We will use the GPU:', torch.cuda.get_device_name(0))

# If not...
else:
    print('No GPU available, using the CPU instead.')
    device = torch.device("cpu")

There are 1 GPU(s) available.
We will use the GPU: Tesla T4


In [ ]:
#installing the library
!pip install pystan==2.19

In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from fbprophet.diagnostics import cross_validation
from fbprophet.diagnostics import performance_metrics
from fbprophet.plot import plot_cross_validation_metric
import itertools
from sklearn.model_selection import train_test_split



#importing library for visualizing
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import warnings 
warnings.filterwarnings('ignore')

In [ ]:
#installing the fbprophet library
!pip install fbprophet

In [ ]:
train=pd.read_csv('/content/drive/MyDrive/jobathon_nov22/train_IxoE5JN.csv')
test=pd.read_csv('/content/drive/MyDrive/jobathon_nov22/test_WudNWDM.csv')
sub=pd.read_csv('/content/drive/MyDrive/jobathon_nov22/sample_submission_jn0a7vR.csv')

In [ ]:
#Using plotly you can se the energy graph
fig = go.Figure([go.Scatter(x=train['datetime'], y=train['energy'])])
fig.show()

In [ ]:
train.isnull().sum().sum()

1900

In [ ]:
train[train['energy'].isnull()==True]

row_id             datetime  energy
92         93  2008-03-04 20:00:00     NaN
207       208  2008-03-09 15:00:00     NaN
217       218  2008-03-10 01:00:00     NaN
448       449  2008-03-19 16:00:00     NaN
519       520  2008-03-22 15:00:00     NaN
...       ...                  ...     ...
94685   94686  2018-12-19 05:00:00     NaN
94722   94723  2018-12-20 18:00:00     NaN
94737   94738  2018-12-21 09:00:00     NaN
94758   94759  2018-12-22 06:00:00     NaN
94857   94858  2018-12-26 09:00:00     NaN

[1900 rows x 3 columns]

In [ ]:
train

row_id             datetime       energy
0           1  2008-03-01 00:00:00  1259.985563
1           2  2008-03-01 01:00:00  1095.541500
2           3  2008-03-01 02:00:00  1056.247500
3           4  2008-03-01 03:00:00  1034.742000
4           5  2008-03-01 04:00:00  1026.334500
...       ...                  ...          ...
94987   94988  2018-12-31 19:00:00  2528.446800
94988   94989  2018-12-31 20:00:00  2461.883600
94989   94990  2018-12-31 21:00:00  2365.994400
94990   94991  2018-12-31 22:00:00  2342.942800
94991   94992  2018-12-31 23:00:00  2180.217600

[94992 rows x 3 columns]

In [ ]:
train['datetime']=pd.to_datetime(train['datetime'])

In [ ]:
train['year']=train['datetime'].dt.year
train['month']=train['datetime'].dt.month
train['day']=train['datetime'].dt.day
train['hour']=train['datetime'].dt.hour

In [ ]:
train1=train[['datetime','energy']]

In [ ]:
train1.rename(columns={'datetime':'ds','energy':'y'},inplace=True)

In [ ]:
from fbprophet import Prophet

m = Prophet(yearly_seasonality = True, seasonality_prior_scale=0.1,changepoint_range=0.9)
m.fit(train1)
future = m.make_future_dataframe(periods=1095,freq='h')
forecast = m.predict(future)

In [ ]:
forecast

ds        trend   yhat_lower   yhat_upper  trend_lower  \
0     2008-03-01 00:00:00  1435.330366   966.634120  1410.002849  1435.330366   
1     2008-03-01 01:00:00  1435.285295   889.785807  1325.374834  1435.285295   
2     2008-03-01 02:00:00  1435.240224   812.363870  1262.446659  1435.240224   
3     2008-03-01 03:00:00  1435.195153   798.571779  1224.583727  1435.195153   
4     2008-03-01 04:00:00  1435.150082   761.831047  1226.036365  1435.150082   
...                   ...          ...          ...          ...          ...   
96082 2019-02-15 10:00:00  2107.521327  1867.973933  2291.585514  2103.137930   
96083 2019-02-15 11:00:00  2107.535636  1886.658570  2305.847470  2103.140948   
96084 2019-02-15 12:00:00  2107.549944  1869.030420  2292.117569  2103.143966   
96085 2019-02-15 13:00:00  2107.564253  1874.596137  2318.358526  2103.146983   
96086 2019-02-15 14:00:00  2107.578561  1897.479953  2324.003194  2103.150001   

       trend_upper  additive_terms  additive_terms_lower  \
0      1435.330366     -242.045669           -242.045669   
1      1435.285295     -327.042499           -327.042499   
2      1435.240224     -391.801396           -391.801396   
3      1435.195153     -429.606260           -429.606260   
4      1435.150082     -435.251990           -435.251990   
...            ...             ...                   ...   
96082  2109.158766      -27.304926            -27.304926   
96083  2109.177597      -15.495837            -15.495837   
96084  2109.196428       -8.691960             -8.691960   
96085  2109.215259       -0.873009             -0.873009   
96086  2109.234090        5.035836              5.035836   

       additive_terms_upper       daily  ...     weekly  weekly_lower  \
0               -242.045669  -80.497133  ...  54.737518     54.737518   
1               -327.042499 -164.274679  ...  53.626603     53.626603   
2               -391.801396 -227.719849  ...  52.421170     52.421170   
3               -429.606260 -264.106182  ...  51.110857     51.110857   
4               -435.251990 -268.217390  ...  49.684475     49.684475   
...                     ...         ...  ...        ...           ...   
96082            -27.304926   75.059654  ...  63.729798     63.729798   
96083            -15.495837   87.418315  ...  63.425321     63.425321   
96084             -8.691960   94.824699  ...  63.066925     63.066925   
96085             -0.873009  103.296912  ...  62.656792     62.656792   
96086              5.035836  109.907971  ...  62.196728     62.196728   

       weekly_upper      yearly  yearly_lower  yearly_upper  \
0         54.737518 -216.286053   -216.286053   -216.286053   
1         53.626603 -216.394423   -216.394423   -216.394423   
2         52.421170 -216.502717   -216.502717   -216.502717   
3         51.110857 -216.610935   -216.610935   -216.610935   
4         49.684475 -216.719074   -216.719074   -216.719074   
...             ...         ...           ...           ...   
96082     63.729798 -166.094378   -166.094378   -166.094378   
96083     63.425321 -166.339473   -166.339473   -166.339473   
96084     63.066925 -166.583584   -166.583584   -166.583584   
96085     62.656792 -166.826713   -166.826713   -166.826713   
96086     62.196728 -167.068863   -167.068863   -167.068863   

       multiplicative_terms  multiplicative_terms_lower  \
0                       0.0                         0.0   
1                       0.0                         0.0   
2                       0.0                         0.0   
3                       0.0                         0.0   
4                       0.0                         0.0   
...                     ...                         ...   
96082                   0.0                         0.0   
96083                   0.0                         0.0   
96084                   0.0                         0.0   
96085                   0.0                         0.0   
96086                   0.0                   

In [ ]:
test1=pd.DataFrame()

In [ ]:
test1['row_id']=test['row_id']

In [ ]:
test.rename(columns={'datetime':'ds'},inplace=True)

In [ ]:
forecast1 = m.predict(df=test)

In [ ]:
forecast1

ds        trend   yhat_lower   yhat_upper  trend_lower  \
0     2019-01-01 00:00:00  2091.925167  1831.653482  2260.823619  2091.925167   
1     2019-01-01 01:00:00  2091.939475  1750.220749  2182.928633  2091.939475   
2     2019-01-01 02:00:00  2091.953784  1711.668219  2129.147071  2091.953784   
3     2019-01-01 03:00:00  2091.968092  1654.778959  2113.031107  2091.968092   
4     2019-01-01 04:00:00  2091.982400  1656.592886  2090.405187  2091.982400   
...                   ...          ...          ...          ...          ...   
26299 2021-12-31 19:00:00  2468.221889  -618.864967  6401.151403 -1013.831901   
26300 2021-12-31 20:00:00  2468.236198  -747.398602  6383.934301 -1014.100441   
26301 2021-12-31 21:00:00  2468.250506  -790.304413  6318.489891 -1014.368981   
26302 2021-12-31 22:00:00  2468.264815  -728.146172  6319.060045 -1014.637520   
26303 2021-12-31 23:00:00  2468.279123  -898.648402  6175.076594 -1014.906060   

       trend_upper  additive_terms  additive_terms_lower  \
0      2091.925167      -47.931573            -47.931573   
1      2091.939475     -123.391892           -123.391892   
2      2091.953784     -178.511572           -178.511572   
3      2091.968092     -206.610644           -206.610644   
4      2091.982400     -202.518179           -202.518179   
...            ...             ...                   ...   
26299  6015.989844      300.519497            300.519497   
26300  6016.127843      313.558487            313.558487   
26301  6016.381157      297.904641            297.904641   
26302  6016.700655      244.874084            244.874084   
26303  6017.020154      162.392475            162.392475   

       additive_terms_upper       daily  ...     weekly  weekly_lower  \
0                -47.931573  -80.497133  ... -63.723204    -63.723204   
1               -123.391892 -164.274679  ... -55.187885    -55.187885   
2               -178.511572 -227.719849  ... -46.644405    -46.644405   
3               -206.610644 -264.106182  ... -38.139262    -38.139262   
4               -202.518179 -268.217390  ... -29.717825    -29.717825   
...                     ...         ...  ...        ...           ...   
26299            300.519497  145.280978  ...  59.167846     59.167846   
26300            313.558487  159.296743  ...  58.409062     58.409062   
26301            297.904641  144.677521  ...  57.592320     57.592320   
26302            244.874084   92.744554  ...  56.712495     56.712495   
26303            162.392475   11.429734  ...  55.763343     55.763343   

       weekly_upper     yearly  yearly_lower  yearly_upper  \
0        -63.723204  96.288764     96.288764     96.288764   
1        -55.187885  96.070673     96.070673     96.070673   
2        -46.644405  95.852682     95.852682     95.852682   
3        -38.139262  95.634800     95.634800     95.634800   
4        -29.717825  95.417036     95.417036     95.417036   
...             ...        ...           ...           ...   
26299     59.167846  96.070673     96.070673     96.070673   
26300     58.409062  95.852682     95.852682     95.852682   
26301     57.592320  95.634800     95.634800     95.634800   
26302     56.712495  95.417036     95.417036     95.417036   
26303     55.763343  95.199398     95.199398     95.199398   

       multiplicative_terms  multiplicative_terms_lower  \
0                       0.0                         0.0   
1                       0.0                         0.0   
2                       0.0                         0.0   
3                       0.0                         0.0   
4                       0.0                         0.0   
...                     ...                         ...   
26299                   0.0                         0.0   
26300                   0.0                         0.0   
26301                   0.0                         0.0   
26302                   0.0                         0.0   
26303                   0.0                         0.0   

In [ ]:
forecast1['yhat']

0        2043.993594
1        1968.547583
2        1913.442211
3        1885.357448
4        1889.464221
            ...     
26299    2768.741387
26300    2781.794685
26301    2766.155147
26302    2713.138899
26303    2630.671598
Name: yhat, Length: 26304, dtype: float64

In [ ]:
test['energy']=forecast1['yhat']

In [ ]:
sub1=test[['row_id','energy']]

In [ ]:
sub1.to_csv('sub1.csv',index=False)

In [ ]:
#Observing the Plot After prediction for test data
fig = go.Figure([go.Scatter(x=test['ds'], y=forecast1['yhat'])])
fig.show()

In [ ]:
fig1 = m.plot(forecast)

fig2 = m.plot_components(forecast)

df_cv = cross_validation(m, initial='730 days', period='90 days', horizon = '180 days')
df_p = performance_metrics(df_cv)
df_p

fig3 = plot_cross_validation_metric(df_cv, metric='rmse')

n_changepoints is the number of change happen in the data. Prophet model detects them by its own. By default, its value is 25, which are uniformly placed in the first 80% of the time series. Changing n_changepoints can add value to the model.

changepoint_prior_scale to indicate how flexible the changepoints are allowed to be. In other words, how much can the changepoints fit to the data. If you make it high it will be more flexible, but you can end up overfitting. By default, this parameter is set to 0.05

seasonality_mode There are 2 types model seasonality mode. Additive & multiplicaticative. By default Prophet fits additive seasonalities, meaning the effect of the seasonality is added to the trend to get the forecast. Prophet can model multiplicative seasonality by setting seasonality_mode='multiplicative' in the model.

holiday_prior_scale just like changepoint_prior_scale, holiday_prior_scale is used to smoothning the effect of holidays. By default its value is 10, which provides very little regularization. Reducing this parameter dampens holiday effects

Seasonalities with fourier_order Prophet model, by default finds the seasonalities and adds the default parameters of the seasonality. We can modify the seasonalities effect by adding custom seasonalities as add_seasonality in the model with different fourier order.Yy default Prophet uses a Fourier order of 3 for weekly seasonality and 10 for yearly seasonality.

Now, we will do the hyperparameters tuning using parametergrid. parametergrid will create all the possible parameters combination and will test the model prediction using every combination. I am taking 4 parameters: n_changepoints, changepoint_prior_scale,seasonality_mode, holiday_prior_scale for tuning.

# HyperParameter Tuning using  ParameterGrid

In [ ]:
from sklearn.model_selection import ParameterGrid
params_grid = {'seasonality_mode':['additive'],
               'changepoint_prior_scale':[0.1,0.2,0.3,0.4,0.5],
               'n_changepoints' : [100,150,200]}
grid = ParameterGrid(params_grid)
cnt = 0
for p in grid:
    print(p)
    cnt = cnt+1

print('Total Possible Models',cnt)

{'changepoint_prior_scale': 0.1, 'n_changepoints': 100, 'seasonality_mode': 'additive'}
{'changepoint_prior_scale': 0.1, 'n_changepoints': 150, 'seasonality_mode': 'additive'}
{'changepoint_prior_scale': 0.1, 'n_changepoints': 200, 'seasonality_mode': 'additive'}
{'changepoint_prior_scale': 0.2, 'n_changepoints': 100, 'seasonality_mode': 'additive'}
{'changepoint_prior_scale': 0.2, 'n_changepoints': 150, 'seasonality_mode': 'additive'}
{'changepoint_prior_scale': 0.2, 'n_changepoints': 200, 'seasonality_mode': 'additive'}
{'changepoint_prior_scale': 0.3, 'n_changepoints': 100, 'seasonality_mode': 'additive'}
{'changepoint_prior_scale': 0.3, 'n_changepoints': 150, 'seasonality_mode': 'additive'}
{'changepoint_prior_scale': 0.3, 'n_changepoints': 200, 'seasonality_mode': 'additive'}
{'changepoint_prior_scale': 0.4, 'n_changepoints': 100, 'seasonality_mode': 'additive'}
{'changepoint_prior_scale': 0.4, 'n_changepoints': 150, 'seasonality_mode': 'additive'}
{'changepoint_prior_scale': 0.4,

In [ ]:
print(train['datetime'].max())
print(train['datetime'].min())

2018-12-31 23:00:00
2008-03-01 00:00:00


In [ ]:
test.drop(columns={'energy'},axis=1,inplace=True)


In [ ]:
from sklearn.metrics import mean_squared_error
import random
import math

In [ ]:
train=train1.dropna()

In [ ]:
train1['ds'].value_counts()

2008-03-01 00:00:00    1
2015-05-22 13:00:00    1
2015-05-22 22:00:00    1
2015-05-22 21:00:00    1
2015-05-22 20:00:00    1
                      ..
2011-10-11 05:00:00    1
2011-10-11 04:00:00    1
2011-10-11 03:00:00    1
2011-10-11 02:00:00    1
2018-12-31 23:00:00    1
Name: ds, Length: 94992, dtype: int64

In [ ]:
train1['ds']=pd.to_datetime(train1['ds'])

In [ ]:
end_date='2015-05-22'
mask1 = (train1['ds'] <= end_date)
mask2 = (train1['ds'] > end_date)

X_tr = train1.loc[mask1]
X_tst = train1.loc[mask2]
print("train shape",X_tr.shape)
print("test shape",X_tst.shape)

X_tst

train shape (63313, 2)
test shape (31679, 2)


ds          y
63313 2015-05-22 01:00:00  1722.1260
63314 2015-05-22 02:00:00  1673.2980
63315 2015-05-22 03:00:00  1648.0076
63316 2015-05-22 04:00:00  1645.5036
63317 2015-05-22 05:00:00  1682.1872
...                   ...        ...
94987 2018-12-31 19:00:00  2528.4468
94988 2018-12-31 20:00:00  2461.8836
94989 2018-12-31 21:00:00  2365.9944
94990 2018-12-31 22:00:00  2342.9428
94991 2018-12-31 23:00:00  2180.2176

[31679 rows x 2 columns]

In [ ]:
mask1

0         True
1         True
2         True
3         True
4         True
         ...  
94987    False
94988    False
94989    False
94990    False
94991    False
Name: ds, Length: 94992, dtype: bool

In [ ]:
# strt='2015-05-22'
# end='2018-12-31'
# model_parameters = pd.DataFrame(columns = ['RMSE','Parameters'])
# for p in grid:
#     test = pd.DataFrame()
#     print(p)
#     random.seed(0)
#     train_model =Prophet(changepoint_prior_scale = p['changepoint_prior_scale'],
#                          n_changepoints = p['n_changepoints'],
#                          seasonality_mode = p['seasonality_mode'],
#                          weekly_seasonality=True,
#                          daily_seasonality = True,
#                         #  yearly_seasonality = True,
#                          interval_width=0.95)
#     train_model.fit(X_tr)
#     # train_forecast = train_model.make_future_dataframe(periods=1095, freq='h',include_history = False)
#     train_forecast = train_model.predict(X_tst)
#     test=train_forecast[['ds','yhat']]
#     Actual = train1[(train1['ds']>strt) & (train1['ds']<=end)]
#     mse = mean_squared_error(Actual['y'], abs(test['yhat']))
#     rmse = math.sqrt(mse)
#     print('Root mean squared error(RMSE)------------------------------------',rmse)
#     model_parameters = model_parameters.append({'rmse':rmse,'Parameters':p},ignore_index=True)

In [ ]:
final_model = Prophet(changepoint_prior_scale= 0.2,
                      n_changepoints = 200,
                      seasonality_mode = 'additive',
                      weekly_seasonality=True,
                      daily_seasonality = True,
                      yearly_seasonality = True,
                      interval_width=0.95)
final_model.fit(train1)

In [ ]:
forecast3=final_model.predict(test)